# Databricks with Flourish Visulization on Daily bar chart race

## Bar Chart Race
In the modern data world, it is quite often for a data person to generate a graph/chart/plot that can tell a story to visually appeal to a great mass of the audience. The bar chart race comes into today's storytelling, and it has become very  popular. Because it helps us visualize the change in trends over time, especially on social media, as they provide a holistic data story/insight in a concise and easy-to-understand chart.

## Notebook objectives:
By the end of this notebook, you should be able to:
+ Import the Covid-19 dataset using Pyspark
+ Learn how the use split, agg, filter, where and pivot funtions on data maniplution
+ Generate the bar chart race visulization via Flourish (Code free)
+ Generate the bar chart race visulation via Python (Automation)

In [0]:
displayHTML("""
<div class="flourish-embed flourish-bar-chart-race" data-src="visualisation/12405668"><script src="https://public.flourish.studio/resources/embed.js"></script></div>
""")

## Import the data
+ Take a glance at the dataset to understand the schma
+ Define the schma and Read the dataset with inferSchema = True

In [0]:
#%fs ls databricks-datasets/COVID/CSSEGISandData/csse_covid_19_data/csse_covid_19_daily_reports/

In [0]:
#%fs head /databricks-datasets/COVID/CSSEGISandData/csse_covid_19_data/csse_covid_19_daily_reports/01-01-2021.csv

In [0]:
from pyspark.sql.types import StructType, StructField, IntegerType, StringType, DoubleType, DateType, TimestampType
schema = StructType([
  StructField('FIPS', IntegerType(), True), 
  StructField('Admin2', StringType(), True),
  StructField('Province_State', StringType(), True),  
  StructField('Country_Region', StringType(), True),  
  StructField('Last_Update', TimestampType(), True),  
  StructField('Lat', DoubleType(), True),  
  StructField('Long_', DoubleType(), True),
  StructField('Confirmed', IntegerType(), True), 
  StructField('Deaths', IntegerType(), True), 
  StructField('Recovered', IntegerType(), True), 
  StructField('Active', IntegerType(), True),   
  StructField('Combined_Key', StringType(), True),  
  StructField('process_date', DateType(), True),    
])

# Create initial empty Spark DataFrame based on preceding schema
jhu_daily = spark.createDataFrame([], schema)

In [0]:
import os
import pandas as pd
import glob
from pyspark.sql.functions import input_file_name, lit, col

# Creates a list of all csv files
globbed_files = glob.glob("/dbfs/databricks-datasets/COVID/CSSEGISandData/csse_covid_19_data/csse_covid_19_daily_reports/*.csv") 

i = 0
for csv in globbed_files:
  # Filename
  source_file = csv[5:200]
  process_date = csv[100:104] + "-" + csv[94:96] + "-" + csv[97:99]
  
  # Read data into temporary dataframe
  df_tmp = spark.read.option("inferSchema", True).option("header", True).csv(source_file)
  df_tmp.createOrReplaceTempView("df_tmp")

  # Obtain schema
  schema_txt = ' '.join(map(str, df_tmp.columns)) 
  
  # Three schema types (as of 2020-04-08) 
  schema_01 = "Province/State Country/Region Last Update Confirmed Deaths Recovered" # 01-22-2020 to 02-29-2020
  schema_02 = "Province/State Country/Region Last Update Confirmed Deaths Recovered Latitude Longitude" # 03-01-2020 to 03-21-2020
  schema_03 = "FIPS Admin2 Province_State Country_Region Last_Update Lat Long_ Confirmed Deaths Recovered Active Combined_Key" # 03-22-2020 to 05-28-2020
  
  # Insert data based on schema type
  if (schema_txt == schema_01):
    df_tmp = (df_tmp
                .withColumn("FIPS", lit(None).cast(IntegerType()))
                .withColumn("Admin2", lit(None).cast(StringType()))
                .withColumn("Province_State", col("Province/State"))
                .withColumn("Country_Region", col("Country/Region"))
                .withColumn("Last_Update", col("Last Update"))
                .withColumn("Lat", lit(None).cast(DoubleType()))
                .withColumn("Long_", lit(None).cast(DoubleType()))
                .withColumn("Active", lit(None).cast(IntegerType()))
                .withColumn("Combined_Key", lit(None).cast(StringType()))
                .withColumn("process_date", lit(process_date))
                .select("FIPS", 
                        "Admin2", 
                        "Province_State", 
                        "Country_Region", 
                        "Last_Update", 
                        "Lat", 
                        "Long_", 
                        "Confirmed", 
                        "Deaths", 
                        "Recovered", 
                        "Active", 
                        "Combined_Key", 
                        "process_date")
               )
    jhu_daily = jhu_daily.union(df_tmp)
  elif (schema_txt == schema_02):
    df_tmp = (df_tmp
                .withColumn("FIPS", lit(None).cast(IntegerType()))
                .withColumn("Admin2", lit(None).cast(StringType()))
                .withColumn("Province_State", col("Province/State"))
                .withColumn("Country_Region", col("Country/Region"))
                .withColumn("Last_Update", col("Last Update"))
                .withColumn("Lat", col("Latitude"))
                .withColumn("Long_", col("Longitude"))
                .withColumn("Active", lit(None).cast(IntegerType()))
                .withColumn("Combined_Key", lit(None).cast(StringType()))
                .withColumn("process_date", lit(process_date))
                .select("FIPS", 
                        "Admin2", 
                        "Province_State", 
                        "Country_Region", 
                        "Last_Update", 
                        "Lat", 
                        "Long_", 
                        "Confirmed", 
                        "Deaths", 
                        "Recovered", 
                        "Active", 
                        "Combined_Key", 
                        "process_date")
               )
    jhu_daily = jhu_daily.union(df_tmp)

  elif (schema_txt == schema_03):
    df_tmp = df_tmp.withColumn("process_date", lit(process_date))
    jhu_daily = jhu_daily.union(df_tmp)
  else:
    print("Schema may have changed")
    print(schema_txt)
    #raise
  
  # print out the schema being processed by date
  print("%s | %s" % (process_date, schema_txt))

Schema may have changed
FIPS Admin2 Province_State Country_Region Last_Update Lat Long_ Confirmed Deaths Recovered Active Combined_Key Incident_Rate Case_Fatality_Ratio
2021-01-01 | FIPS Admin2 Province_State Country_Region Last_Update Lat Long_ Confirmed Deaths Recovered Active Combined_Key Incident_Rate Case_Fatality_Ratio
Schema may have changed
FIPS Admin2 Province_State Country_Region Last_Update Lat Long_ Confirmed Deaths Recovered Active Combined_Key Incident_Rate Case_Fatality_Ratio
2021-01-02 | FIPS Admin2 Province_State Country_Region Last_Update Lat Long_ Confirmed Deaths Recovered Active Combined_Key Incident_Rate Case_Fatality_Ratio
Schema may have changed
FIPS Admin2 Province_State Country_Region Last_Update Lat Long_ Confirmed Deaths Recovered Active Combined_Key Incident_Rate Case_Fatality_Ratio
2021-01-03 | FIPS Admin2 Province_State Country_Region Last_Update Lat Long_ Confirmed Deaths Recovered Active Combined_Key Incident_Rate Case_Fatality_Ratio
Schema may have cha

In [0]:
display(jhu_daily)

FIPS Admin2 Province_State Country_Region Last_Update Lat Long_ Confirmed Deaths Recovered Active Combined_Key process_date null null Anhui Mainland China 1/22/2020 17:00 null null 1 null null null null 2020-01-22 null null Beijing Mainland China 1/22/2020 17:00 null null 14 null null null null 2020-01-22 null null Chongqing Mainland China 1/22/2020 17:00 null null 6 null null null null 2020-01-22 null null Fujian Mainland China 1/22/2020 17:00 null null 1 null null null null 2020-01-22 null null Gansu Mainland China 1/22/2020 17:00 null null null null null null null 2020-01-22 null null Guangdong Mainland China 1/22/2020 17:00 null null 26 null null null null 2020-01-22 null null Guangxi Mainland China 1/22/2020 17:00 null null 2 null null null null 2020-01-22 null null Guizhou Mainland China 1/22/2020 17:00 null null 1 null null null null 2020-01-22 null null Hainan Mainland China 1/22/2020 17:00 null null 4 null null null null 2020-01-22 null null Hebei Mainland China 1/22/2020 17:00 null null 1 null null null null 2020-01-22 null null Heilongjiang Mainland China 1/22/2020 17:00 null null null null null null null 2020-01-22 null null Henan Mainland China 1/22/2020 17:00 null null 5 null null null null 2020-01-22 null null Hong Kong Hong Kong 1/22/2020 17:00 null null null null null null null 2020-01-22 null null Hubei Mainland China 1/22/2020 17:00 null null 444 17 28.0 null null 2020-01-22 null null Hunan Mainland China 1/22/2020 17:00 null null 4 null null null null 2020-01-22 null null Inner Mongolia Mainland China 1/22/2020 17:00 null null null null null null null 2020-01-22 null null Jiangsu Mainland China 1/22/2020 17:00 null null 1 null null null null 2020-01-22 null null Jiangxi Mainland China 1/22/2020 17:00 null null 2 null null null null 2020-01-22 null null Jilin Mainland China 1/22/2020 17:00 null null null null null null null 2020-01-22 null null Liaoning Mainland China 1/22/2020 17:00 null null 2 null null null null 2020-01-22 null null Macau Macau 1/22/2020 17:00 null null 1 null null null null 2020-01-22 null null Ningxia Mainland China 1/22/2020 17:00 null null 1 null null null null 2020-01-22 null null Qinghai Mainland China 1/22/2020 17:00 null null null null null null null 2020-01-22 null null Shaanxi Mainland China 1/22/2020 17:00 null null null null null null null 2020-01-22 null null Shandong Mainland China 1/22/2020 17:00 null null 2 null null null null 2020-01-22 null null Shanghai Mainland China 1/22/2020 17:00 null null 9 null null null null 2020-01-22 null null Shanxi Mainland China 1/22/2020 17:00 null null 1 null null null null 2020-01-22 null null Sichuan Mainland China 1/22/2020 17:00 null null 5 null null null null 2020-01-22 null null Taiwan Taiwan 1/22/2020 17:00 null null 1 null null null null 2020-01-22 null null Tianjin Mainland China 1/22/2020 17:00 null null 4 null null null null 2020-01-22 null null Tibet Mainland China 1/22/2020 17:00 null null null null null null null 2020-01-22 null null Washington US 1/22/2020 17:00 null null 1 null null null null 2020-01-22 null null Xinjiang Mainland China 1/22/2020 17:00 null null null null null null null 2020-01-22 null null Yunnan Mainland China 1/22/2020 17:00 null null 1 null null null null 2020-01-22 null null Zhejiang Mainland China 1/22/2020 17:00 null null 10 null null null null 2020-01-22 null null null Japan 1/22/2020 17:00 null null 2 null null null null 2020-01-22 null null null Thailand 1/22/2020 17:00 null null 4 0 2.0 null null 2020-01-22 null null null South Korea 1/22/2020 17:00 null null 1 null null null null 2020-01-22 null null Anhui Mainland China 1/23/20 17:00 null null 9 null null null null 2020-01-23 null null Beijing Mainland China 1/23/20 17:00 null null 22 null null null null 2020-01-23 null null Chongqing Mainland China 1/23/20 17:00 null null 9 null null null null 2020-01-23 null null Fujian Mainland China 1/23/20 17:00 null null 5 null null null null 2020-01-23 null null Gansu Mainland China 1/23/20 17:00 null nu

## Data Manipulation
+ Filter out the data for US only and eliminate all the null values
+ Impute all the unreported days/states as 0 
+ Aggreagte the total number of confirmed case breakdown by states and days
+ Pivote the table from long to wide forat that can be directly digest by Flourish

In [0]:
#Import libraries 
import pyspark.pandas as pd
import numpy as np
from pyspark.sql.functions import expr, col, split

# Fliter the US data only before aggregation
df = jhu_daily.where(jhu_daily.Country_Region == 'US')
df = df.dropna()

# Get the State information from Combined_Key
df = df.withColumn("State_abbr", split(df['Combined_Key'], ',').getItem(1))
display(df)

FIPS Admin2 Province_State Country_Region Last_Update Lat Long_ Confirmed Deaths Recovered Active Combined_Key process_date State_abbr 36061 New York City New York US 3/22/20 23:45 40.7672726 -73.97152637 9654 63 0.0 0 New York City, New York, US 2020-03-22 New York 36059 Nassau New York US 3/22/20 23:45 40.74066522 -73.58941873 1900 4 0.0 0 Nassau, New York, US 2020-03-22 New York 36119 Westchester New York US 3/22/20 23:45 41.16278376 -73.75741653 1873 0 0.0 0 Westchester, New York, US 2020-03-22 New York 36103 Suffolk New York US 3/22/20 23:45 40.88320119 -72.8012172 1034 9 0.0 0 Suffolk, New York, US 2020-03-22 New York 36087 Rockland New York US 3/22/20 23:45 41.15027894 -74.02560498 455 1 0.0 0 Rockland, New York, US 2020-03-22 New York 36071 Orange New York US 3/22/20 23:45 41.40337468 -74.30240757 247 0 0.0 0 Orange, New York, US 2020-03-22 New York 36001 Albany New York US 3/22/20 23:45 42.60060306 -73.97723916 123 0 0.0 0 Albany, New York, US 2020-03-22 New York 36027 Dutchess New York US 3/22/20 23:45 41.7648606 -73.74356679 82 0 0.0 0 Dutchess, New York, US 2020-03-22 New York 36055 Monroe New York US 3/22/20 23:45 43.14638895 -77.69322942 68 1 0.0 0 Monroe, New York, US 2020-03-22 New York 36029 Erie New York US 3/22/20 23:45 42.76249024 -78.73063652 56 0 0.0 0 Erie, New York, US 2020-03-22 New York 36067 Onondaga New York US 3/22/20 23:45 43.00491923 -76.19971155 45 0 0.0 0 Onondaga, New York, US 2020-03-22 New York 36091 Saratoga New York US 3/22/20 23:45 43.10904162 -73.86653895 35 0 0.0 0 Saratoga, New York, US 2020-03-22 New York 36093 Schenectady New York US 3/22/20 23:45 42.81668777 -74.05278291 32 0 0.0 0 Schenectady, New York, US 2020-03-22 New York 36079 Putnam New York US 3/22/20 23:45 41.42630093 -73.74965532 31 0 0.0 0 Putnam, New York, US 2020-03-22 New York 36083 Rensselaer New York US 3/22/20 23:45 42.71348136 -73.51089874 20 0 0.0 0 Rensselaer, New York, US 2020-03-22 New York 36111 Ulster New York US 3/22/20 23:45 41.89027881 -74.26252104 18 0 0.0 0 Ulster, New York, US 2020-03-22 New York 36021 Columbia New York US 3/22/20 23:45 42.24819348 -73.63089095 17 0 0.0 0 Columbia, New York, US 2020-03-22 New York 36109 Tompkins New York US 3/22/20 23:45 42.44945765 -76.47229843 15 0 0.0 0 Tompkins, New York, US 2020-03-22 New York 36105 Sullivan New York US 3/22/20 23:45 41.71579493 -74.76394559 12 0 0.0 0 Sullivan, New York, US 2020-03-22 New York 36063 Niagara New York US 3/22/20 23:45 43.19898042 -78.74777412 9 0 0.0 0 Niagara, New York, US 2020-03-22 New York 36065 Oneida New York US 3/22/20 23:45 43.24375382 -75.43710392 4 0 0.0 0 Oneida, New York, US 2020-03-22 New York 36069 Ontario New York US 3/22/20 23:45 42.85145728 -77.30874425 4 0 0.0 0 Ontario, New York, US 2020-03-22 New York 36019 Clinton New York US 3/22/20 23:45 44.74530905 -73.67875352 4 0 0.0 0 Clinton, New York, US 2020-03-22 New York 36043 Herkimer New York US 3/22/20 23:45 43.42034246 -74.96145307 3 0 0.0 0 Herkimer, New York, US 2020-03-22 New York 36007 Broome New York US 3/22/20 23:45 42.15903158 -75.81326086 3 1 0.0 0 Broome, New York, US 2020-03-22 New York 36057 Montgomery New York US 3/22/20 23:45 42.90123494 -74.44011632 3 0 0.0 0 Montgomery, New York, US 2020-03-22 New York 36031 Essex New York US 3/22/20 23:45 44.11630765 -73.77297842 3 0 0.0 0 Essex, New York, US 2020-03-22 New York 36117 Wayne New York US 3/22/20 23:45 43.15494365 -77.02976528 3 0 0.0 0 Wayne, New York, US 2020-03-22 New York 36039 Greene New York US 3/22/20 23:45 42.275797 -74.12384884 2 0 0.0 0 Greene, New York, US 2020-03-22 New York 36003 Allegany New York US 3/22/20 23:45 42.25748406 -78.02750466 2 0 0.0 0 Allegany, New York, US 2020-03-22 New York 36121 Wyoming New York US 3/22/20 23:45 42.70145109 -78.22199579 2 0 0.0 0 Wyoming, New York, US 2020-03-22 New York 36041 Hamilton New York US 3/22/20 23:45 43.66146647 -74.49721957 2 0 0.0 0 Hamilton, New York, US 2020-03-22 New York 36017 Chenango New York US 3/22/20 23:45 42.49430041 -75.60887553 2

In [0]:
# Fliter the US data only before aggregation
#df = jhu_daily.where(jhu_daily.Country_Region == 'US')
#df = df.dropna()
#generate the state_list
state_list = df.select('State_abbr').distinct().withColumnRenamed("State_abbr","State")
#generate the time_list
time_list = df.select('process_date').distinct().withColumnRenamed("process_date","Date")
#cross join the generate the full table
full_table = time_list.crossJoin(state_list.select("*")).select("*")
#aggregated the daily sum by day and state
agg_daily = df.groupBy("process_date", "State_abbr").agg({'confirmed':'sum'})
# right join the full table and fill the NA values as 0
final = agg_daily.join(full_table, \
                       (agg_daily.process_date == full_table.Date)& \
                       (agg_daily.State_abbr == full_table.State), \
                       'right').na.fill(0, ['sum(confirmed)']).withColumnRenamed("sum(confirmed)","Total")
# convert the long to wide that can be feed into flurish
final_pivot = final.groupBy("State").pivot("Date").sum("Total")

In [0]:
display(final_pivot)

State 2020-03-22 2020-03-23 2020-03-24 2020-03-25 2020-03-26 2020-03-27 2020-03-28 2020-03-29 2020-03-30 2020-03-31 2020-04-01 2020-04-02 2020-04-03 2020-04-04 2020-04-05 2020-04-06 2020-04-07 2020-04-08 2020-04-09 2020-04-10 2020-04-11 2020-04-12 2020-04-13 2020-04-14 2020-04-15 2020-04-16 2020-04-17 2020-04-18 2020-04-19 2020-04-20 2020-04-21 2020-04-22 2020-04-23 2020-04-24 2020-04-25 2020-04-26 2020-04-27 2020-04-28 2020-04-29 2020-04-30 2020-05-01 2020-05-02 2020-05-03 2020-05-04 2020-05-05 2020-05-06 2020-05-07 2020-05-08 2020-05-09 2020-05-10 2020-05-11 2020-05-12 2020-05-13 2020-05-14 2020-05-15 2020-05-16 2020-05-17 2020-05-18 2020-05-19 2020-05-20 2020-05-21 2020-05-22 2020-05-23 2020-05-24 2020-05-25 2020-05-26 2020-05-27 2020-05-28 Kansas 65 84 100 134 172 206 266 330 372 434 485 553 629 698 751 849 912 1046 1116 1117 1275 1344 1390 1441 1504 1615 1730 1821 1905 2048 2164 2331 2721 2959 3135 3277 3473 3652 3839 4413 4634 4885 5156 5383 5648 5993 6332 6667 6829 6951 7159 7240 7518 7705 7886 7939 7953 8303 8353 8507 8625 8909 8946 9004 9125 9199 9291 9371 North Dakota 28 30 36 45 51 68 94 98 109 122 142 159 173 186 207 225 237 251 269 278 293 308 331 341 365 393 393 528 585 627 644 679 709 748 803 867 942 991 1033 1067 1107 1153 1191 1225 1266 1323 1371 1425 1464 1491 1518 1571 1647 1712 1761 1848 1900 1931 1994 2095 2229 2317 2365 2418 2457 2422 2439 2481 Missouri 134 223 301 384 536 701 858 941 1119 1400 1643 1879 1927 2312 2341 2709 3032 3111 3316 3706 3898 4044 4239 4468 4525 4879 5068 5240 5390 5533 5724 5928 6131 6391 6525 6698 6875 7003 7239 7406 7705 7929 8086 8358 8520 8702 8898 9023 9185 9309 9389 9503 9625 9786 9970 10134 10235 10360 10509 10635 10798 10908 11000 11128 11402 11490 11723 11866 Maine 81 102 118 140 154 165 208 248 270 297 297 368 421 444 459 488 510 529 556 583 613 630 693 733 768 794 826 846 865 874 887 905 937 965 965 1013 1021 1039 1054 1094 1123 1153 1185 1203 1226 1254 1328 1368 1407 1433 1456 1471 1509 1563 1601 1646 1685 1712 1740 1817 1874 1945 2013 2054 2074 2109 2134 2184 Pennsylvania 509 698 946 1260 1795 2345 2844 3431 4154 4962 6008 7267 8569 10443 11588 13126 14852 16631 18300 20051 21719 22938 24292 25465 26753 28258 29888 31652 32902 33914 35249 36082 38379 40208 41153 42616 43558 45137 46327 47971 49579 50494 51225 52816 53864 54800 55956 57371 58560 59939 60459 61310 62101 63105 64136 65185 65700 66669 67311 68126 69252 70211 71009 71563 71925 72778 73557 74220 Iowa 90 105 122 146 179 235 298 336 424 495 547 612 696 784 869 946 1046 1145 1270 1388 1510 1587 1710 1899 1995 2141 2331 2512 2895 3157 3620 3744 3921 4441 5087 5470 5861 6363 6823 7121 7821 8548 9051 9608 10111 10391 11051 11440 11668 11959 12368 12906 13284 13667 14039 14313 14643 14946 15291 15612 16156 16486 16896 17248 17551 17701 18361 18585 Ohio 356 443 567 704 868 1137 1406 1653 1933 2199 2547 2901 3312 3738 4041 4449 4780 5146 5509 5875 6250 6602 6975 7285 7794 8414 9107 10222 11602 12919 13725 14117 14694 15169 15587 15972 16325 16769 17303 18027 18743 19335 19914 20474 20969 21576 22131 23016 23697 24081 24777 25250 25721 26357 26954 27474 27923 28454 28952 29436 30167 30794 31408 31911 32477 33006 33439 33915 Louisiana 787 1161 1376 1784 2291 2728 3304 3530 4009 5213 6394 9109 10255 12461 12975 14813 16229 16973 18223 19190 19950 20530 20947 21449 21882 22476 23062 23523 23870 24464 24795 25198 25677 26077 26449 26709 27004 27225 27599 27940 28648 29077 29277 29610 29933 30336 30589 30792 31353 31536 31751 31986 32598 33424 33772 34045 34360 34637 34966 35244 36426 36822 36822 37091 37732 37977 38413 38718 Arizona 152 235 326 401 508 665 773 919 1157 1289 1209 1336 1478 1675 1896 2058 2146 2266 3018 3112 3393 3542 3705 3809 3964 4237 4511 4724 4933 5068 5256 5473 5772 6045 6286 6534 6725 6955 7209 7655 7969 8364 8640 8924 9305 9707 9945 10526 10960 11119 11383 11736 12216 12674 13169 13666 13945 14208 14576 14906 15348 15624 16053 16377 16575 16864 17318 17877 Illinois 1047 1222 1537 1863 1870 3024 3480

## Flourish - Generate the dynamic bar chart
Here, let's follow the steps below to gengete the final video withou any coding effort:
+ Download the final_pivot table above as csv file to your local laptop
+ Log in to your Flourish account here: https://flourish.studio/
+ In the **"My Projects"** space, click on **"New visualization."**
+ Select the **'Bar chart race'** visualization template, once you open it, you will see the **'Preview'** tab and the **'Data'** tab on the top. Click on the **'Data'** tab and then navigate to the right bar on **'Upload Data'**.
+ Upload the data we just downloaded from Databricks and then confirm on **'Import'**. 
+ Once you have uploaded your data, you can select which columns to visualize, adjust the labels, values, and colors, and even filter your data. You should be able to see the previews of the dynamic bar chart race on the bottom right.
+ Once you have done all the modifications, give a name for your visualization on the top left. 
+ To share your visualizations, click on the right top **'Export&publish'** and then click on **'Publish to share and embed'**, then it will generate a weblink or embed source code that allows you to share on other public websites like medium or Tiktok.

In [0]:
displayHTML("""
<div class="flourish-embed flourish-bar-chart-race" data-src="visualisation/12405668"><script src="https://public.flourish.studio/resources/embed.js"></script></div>
""")

## Python - Generate the dynamic bar chart 
Alternativerly, you can use the bar_chart_race library to gengerate the visulization using python code. So that you can automated the whole notebook rather than download the data and manually import into Flourish. The offical docment can be found [here](https://www.dexplo.org/bar_chart_race/)

In [0]:
!pip install bar_chart_race

     |████████████████████████████████| 156 kB 5.4 MB/s 
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-faa50732-6bd8-4b39-a563-0569ef282e89/bin/python -m pip install --upgrade pip' command.


In [0]:
%sh
#!/bin/bash
sudo apt-get update
sudo apt-get -y install ffmpeg

Hit:1 https://repos.azul.com/zulu/deb stable InRelease
Get:2 http://security.ubuntu.com/ubuntu focal-security InRelease [114 kB]
Get:3 http://security.ubuntu.com/ubuntu focal-security/main amd64 Packages [2,423 kB]
Hit:4 http://archive.ubuntu.com/ubuntu focal InRelease
Get:5 http://archive.ubuntu.com/ubuntu focal-updates InRelease [114 kB]
Get:6 http://archive.ubuntu.com/ubuntu focal-backports InRelease [108 kB]
Get:7 http://archive.ubuntu.com/ubuntu focal-updates/main amd64 Packages [2,896 kB]
Get:8 http://security.ubuntu.com/ubuntu focal-security/multiverse amd64 Packages [27.7 kB]
Get:9 http://security.ubuntu.com/ubuntu focal-security/restricted amd64 Packages [1,862 kB]
Get:10 http://security.ubuntu.com/ubuntu focal-security/universe amd64 Packages [979 kB]
Get:11 http://archive.ubuntu.com/ubuntu focal-updates/multiverse amd64 Packages [31.2 kB]
Get:12 http://archive.ubuntu.com/ubuntu focal-updates/restricted amd64 Packages [1,986 kB]
Get:13 http://archive.ubuntu.com/ubuntu focal-u

In [0]:
final_pivot2 = final.groupBy("Date").pivot("State").sum("Total")
final_pivot2 = final_pivot2.toPandas()

display(final_pivot2)

Date Alabama Alaska Arizona Arkansas California Colorado Connecticut Delaware District of Columbia Florida Georgia Hawaii Idaho Illinois Indiana Iowa Kansas Kentucky Louisiana Maine Maryland Massachusetts Michigan Minnesota Mississippi Missouri Montana Nebraska Nevada New Hampshire New Jersey New Mexico New York North Carolina North Dakota Ohio Oklahoma Oregon Pennsylvania Rhode Island South Carolina South Dakota Tennessee Texas Utah Vermont Virginia Washington West Virginia Wisconsin Wyoming Alaska Arizona District of Columbia Florida Georgia Hawaii Idaho Illinois Indiana Iowa Louisiana Michigan Minnesota Missouri Nebraska New Hampshire New Mexico North Carolina Ohio Pennsylvania Tennessee Texas Utah Virginia Washington 2020-04-13 3870 277 3705 1374 23946 7546 12890 1758 1955 21017 12068 499 1426 21939 8359 1710 1390 1906 20947 693 8936 26399 25018 1605 2942 4239 394 791 2990 984 63381 1262 195749 4886 331 6975 2069 1584 24292 1700 3391 868 5294 14328 2260 740 5706 10016 611 3428 275 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 2020-04-12 3667 272 3542 1255 22797 7151 11534 1625 1875 19893 11209 494 1407 20731 7928 1587 1344 1851 20530 630 8225 25081 24014 1605 2781 4044 387 768 2813 928 60576 1245 189033 4570 308 6602 1970 1526 22938 1700 3320 730 5211 13780 2203 720 5240 9877 593 3341 270 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 2020-04-20 5163 321 5068 1928 33946 9616 19301 2714 2927 27056 18160 578 1672 31383 11688 3157 2048 2977 24464 874 13684 37239 31287 2466 4512 5533 433 1611 3794 1443 88137 1971 253060 6895 627 12919 2680 1957 33914 4229 4446 1685 6908 19847 2930 805 8990 11955 902 4499 317 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 2020-05-14 11161 379 12674 4231 75580 20767 35229 7178 6736 43134 33059 627 2351 87786 26053 13667 7705 7194 33424 1563 35903 81846 47168 13414 10483 9786 462 9260 6504 3348 142581 5437 343051 16968 1712 26357 4962 3479 63105 10789 8189 3792 16359 44701 6394 928 27813 17663 1427 11275 701 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 2020-04-22 5692 335 5473 2181 37731 10796 21919 3172 3206 28309 19544 586 1766 34879 12438 3744 2331 3306 25198 905 14775 42067 33214 2718 4894 5928 439 1801 4075 1571 94869 2210 263292 7495 679 14117 2894 2059 36082 4946 4761 1858 7093 21577 3154 820 10266 12437 939 4845 447 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 2020-05-13 10822 379 12216 4096 73603 20390 34605 6916 6584 42314 32582 627 2293 84566 25473 13284 7518 6822 32598 1509 34812 80198 46038 12901 10090 9625 462 8912 6476 3273 141584 5302 340661 16352 1647 25721 4857 3416 62101 10789 8030 3732 15924 43456 6268 925 26746 17439 1398 10902 688 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 2020-04-19 4978 319 4933 1735 31660 9616 17433 2508 2793 26311 17179 574 1668 30242 11211 2895 1905 2881 23870 865 12847 37239 30712 2352 4274 5390 433 1434 3708 1390 84716 1845 247815 6598 585 11602 2567 1910 32902 3676 4377 1635 6708 19282 2799 803 8542 11819 890 4346 313 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 2020-03-26 574 52 508 311 3899 1328 1012 130 0 2352 1359 87 146 1870 645 179 172 143 2291 154 583 2147 2838 341 485 536 90 74 416 137 5398 100 37877 726 51 868 248 316 1795 132 424 46 868 1563 360 150 457 3138 52 728 53 4 0 231 5 0 0 0 0 0 0 0 0 3 0 0 0 13 12 0 0 0 0 22 9 0 2020-05-16 11828 387 13666 4447 79471 21556 36446 7501 7042 44732 33868 629 2419 92325 27280 14313 7939 7657 34045 1646 37968 84587 48083 14941 11123 10134 468 10055 6813 3546 145078 5767 348232 18130 1848 27474 5237 3612 65185 10789 8661 3959 16923 47650 6698 930 29683 18176 1470 12187 741 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 2020-04-25 6274 339 6286 2709 42771 12837 24061 3573 3699 30838 21623 598 1887 41503 14399 5087 3135 3857 26449 965 17766 52571 35946 3441 5718 6525 445 2719 4523 1788 104966 2660 282143 8767 803 15587 3194 2253 41153 5931 5253 2147 8834 24287 3623 838 12366 13182 1010 5687 491 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 2020-05-15 11494 387 13169 43

In [0]:
import ffmpeg
import bar_chart_race as bcr

final_pivot3 = final_pivot2.rename(columns = {'Date':'date'}).set_index(['date'])
bcr.bar_chart_race(final_pivot3,  n_bars=10)

/databricks/python/lib/python3.9/site-packages/matplotlib/backends/backend_agg.py:240: RuntimeWarning: Glyph 127 missing from current font.
  font.set_text(s, 0.0, flags=flags)
/databricks/python/lib/python3.9/site-packages/matplotlib/backends/backend_agg.py:240: RuntimeWarning: Glyph 128 missing from current font.
  font.set_text(s, 0.0, flags=flags)
/databricks/python/lib/python3.9/site-packages/matplotlib/backends/backend_agg.py:240: RuntimeWarning: Glyph 129 missing from current font.
  font.set_text(s, 0.0, flags=flags)
/databricks/python/lib/python3.9/site-packages/matplotlib/backends/backend_agg.py:240: RuntimeWarning: Glyph 130 missing from current font.
  font.set_text(s, 0.0, flags=flags)
/databricks/python/lib/python3.9/site-packages/matplotlib/backends/backend_agg.py:240: RuntimeWarning: Glyph 131 missing from current font.
  font.set_text(s, 0.0, flags=flags)
/databricks/python/lib/python3.9/site-packages/matplotlib/backends/backend_agg.py:240: RuntimeWarning: Glyph 132 mi

Your browser does not support the video tag.